In [3]:
import musx
musx.setmidiplayer("fluidsynth -iq -g1 /Users/taube/Music/SoundFonts/MuseScore_General.sf2")
%pwd

'/Users/taube/Classes/mus305/lectures/spectral'

# Composing with microtones and the harmonic series

For spectral and microtonal composers the harmonic series serves as an unlimited source of inspiration. This notebook demonstrates some of the musx functions that support working with the harmonic series and just intervals.

<img src="support/1300px-Harmonics_to_32.png" alt="support/1300px-Harmonics_to_32.png" width=800\>

### Microtonality and MIDI...

The MIDI key numbers 0-127 define 11 octaves of the *twelve tone equal tempered scale* (12-TET) starting on A00 (keynum 0 at 8.175Hz) and ending at G9 (keynum 127 at 12543.854Hz). Every adjacent interval in the equal tempered scale is the same size -- 2<sup>1/12</sup> -- and is called the *half-step*, the smallest interval in the western tuning.

In contrast, the harmonic series has NO equal tempered interval except (trivially) the octave -- every other interval in the series deviates from equal temperment. Compare, for example, the ratios for the perfect 5th, major third and minor third between the natural harmonic series and 12-TET:


In [1]:
print("P5:", 3/2, ", 12-TET:", 2**(7/12))
print("M3:", 5/4, ", 12-TET:", 2**(4/12))
print("m3:", 6/5, ", 12-TET:", 2**(3/12))

P5: 1.5 , 12-TET: 1.4983070768766815
M3: 1.25 , 12-TET: 1.2599210498948732
m3: 1.2 , 12-TET: 1.189207115002721


From the vantage point of 12-TET, every pitch but the octave in the harmonic series involves **microtones**, i.e. tones that lie somewhere in between two adjacent equal tempered tones.  From the vantage point of the harmonic series, the tones of the equal tempered scale are simply out of tune (not pure).

### MIDI Pitch Bends

Since standard MIDI is 12-TET, playing keys on a midi keyboard will not produce microtones unless modified by another message, called a *pitch bend*, that moves the  frequency of **all the notes sounding on a given channel** higher or lower by some amount.

```MidiEvent.pitch_bend(channel, bend, time=0.0)```

* Channel is the midi channel 0-15.

* Bend is a 14bit quantity (0 to 16383) defining the amount to deviate from equal temperment. The bend value is sometimes described as ranging from -8192 to +8191 with 0 being equal temperment. 

What the bend value actually maps to depends on the MIDI device you are using. The typical mapping is that the lowest bend value equals one whole-step down and the highest value represents one whole step up. But this is only a convention -- some devices will let you set the maximum bend value move an octave up, for example.

Run this example to listen to pitch bends. The pitch bends in the first example sound like individual notes because only 10 pitch bends are used over 3 seconds. The second version uses twice as many pitch bends as the first and sounds more continuous. The last two use 40 bends and sound much smoother.  The last example also demonstrates that pitch bends will affect all the notes that are currently sounding on the pitch bend's channel, rather than on a per-note basis. 

MIDI 2.0 supports [per-note pitch bends](https://www.youtube.com/watch?v=x2QxFnsKWMQ).

In [4]:
import math

def bender(score, length, cycs, rhy, dur, key, amp):
    twopi = 2 * math.pi
    if not isinstance(key, list):
        key = [key]
    for i in range(length):
        if i == 0:
            for k in key:
                n = musx.Note(time=score.now, duration=dur, pitch=k, amplitude=amp)
                score.add(n)
        a = math.sin(twopi * cycs * (i / length))
        b = int(musx.rescale(a, -1, 1, 0, 16383))
        score.add(musx.MidiEvent.pitch_bend(0, b, score.now))
        yield rhy

a = musx.MidiFile.metatrack(ins={0: musx.midi.gm.Flute})
b = musx.Seq()
s = musx.Score(out=b)
s.compose([ [0,  bender(s, 10, 1, .1, 3, 72, .8)],
            [4,  bender(s, 20, 1, .05, 3, 72, .8)],
            [8,  bender(s, 40, 1, .025, 3, 72, .8)],
            [12, bender(s, 40, 1, .025, 3, [72,76,79,81], .8)]
          ])
#b.print()
f=musx.MidiFile("bender.mid", [a,b]).write()       
musx.playfile(f.pathname)

### musx channel tuning

As can be seen in the above example, working with pitch bends directly can be rather unwieldy. To help facilitate working with non 12-TET tunings, musx provides two features, that when used together, allow composers to more easily approxiate microtonal scales and tunings. 

The first feature is musx's floating point key numbers *kkk.cc* where *kkk* is the midi key number and *cc* is interpreted as cents above the midi key *kkk*. For example, the keynum 60.5 specifies a pitch that is 50 cents (one 1/4 tone) above the equal tempered tuning. Since a semitone is 100 cents, any microtonal value can be encoded as a floating point keynum.  

The second feature, called *channel tuning*, implements a fixed, microtonal setup for an entire midi file. Microtuning is activated by using the *microdivs* argument to *metatrack()*. The microdivs option quantizes the semitone into some number of micro-divisions. The default value for *microdivs* is 1, which means that the semitone is divided by 1, so no microtonal output occurs. However, if microdivs is 2 then semitone/2 = 50 cent quantization (quartertone tuning), and so on. The maxmimum number for microdivs is 16, or 6.25 cents, which is very close to the frequency limen of ~5 cents. 

Channel tuning works by claiming certain channels to use for microtonal inflection. For example, if microdivs is 2 then channel tuning claims successive *pairs* of channels for quarter-tone tuning:

channels:      | chan0 | chan1 | chan2 | chan3 | ... |
---------------|-------|-------|-------|-------|-----|
tuning (cents):| 0     | 50    | 0     | 50    | ... |
instrument:    | flute | flute | viola | viola | ... |

This means that the channels available for different instuments are 0, 2, 4, 6, 8, 10, 12, and 14, and the channels 1 3 5 6 9 11 13 15 will be assigned to same instrument as their left side channel but tuned one 1/4 tone higher. This means that any fractional key number value .5 or greater that is written to the midi file on channel 0 will be automatically routed to the second channel in the pair (channel 1). A microdivs of 16 will claim all 16 channels in order to produce microtones so the only channel available for instrument assignment will be channel 0. For more information see the micro.py demo file.

In [5]:
def play_micro_divisions(divs):
    """
    Plays one octave of microtones quantized to 1/divs semitones.
    """
    def playmicro(score, key, rhy, divs):
        inc = 1/divs
        for i in range(12 * divs + 1):
            note = musx.Note(time=score.now, duration=rhy, pitch=key)
            score.add(note)
            key += inc
            yield rhy
     
    track0 = musx.MidiFile.metatrack(microdivs=divs) # divs can range 1 to 16
    track1 = musx.Seq()
    score = musx.Score(out=track1)
    score.compose(playmicro(score, 60, .5, divs))
    file = musx.MidiFile("microdivs.mid", [track0, track1]).write()
    track0.print()
    musx.playfile(file.pathname)

In [6]:
# floating point key numbers quantized to quarter tones (24-TET tuning)
play_micro_divisions(2)

0	0.0	[255, 81, 3, 15, 66, 64]
1	0.0	[255, 88, 4, 4, 2, 24, 8]
2	0.0	[255, 89, 2, 0, 0]
3	0.0	[192, 0]
4	0.0	[193, 0]
5	0.0	[194, 0]
6	0.0	[195, 0]
7	0.0	[196, 0]
8	0.0	[197, 0]
9	0.0	[198, 0]
10	0.0	[199, 0]
11	0.0	[200, 0]
12	0.0	[201, 0]
13	0.0	[202, 0]
14	0.0	[203, 0]
15	0.0	[204, 0]
16	0.0	[205, 0]
17	0.0	[206, 0]
18	0.0	[207, 0]
19	0.0	[224, 0, 64]
20	0.0	[225, 127, 79]
21	0.0	[226, 0, 64]
22	0.0	[227, 127, 79]
23	0.0	[228, 0, 64]
24	0.0	[229, 127, 79]
25	0.0	[230, 0, 64]
26	0.0	[231, 127, 79]
27	0.0	[232, 0, 64]
28	0.0	[233, 127, 79]
29	0.0	[234, 0, 64]
30	0.0	[235, 127, 79]
31	0.0	[236, 0, 64]
32	0.0	[237, 127, 79]
33	0.0	[238, 0, 64]
34	0.0	[239, 127, 79]


In [7]:
# floating point key numbers quantized to ~16 cents (72-TET tuning)
play_micro_divisions(6)

0	0.0	[255, 81, 3, 15, 66, 64]
1	0.0	[255, 88, 4, 4, 2, 24, 8]
2	0.0	[255, 89, 2, 0, 0]
3	0.0	[192, 0]
4	0.0	[193, 0]
5	0.0	[194, 0]
6	0.0	[195, 0]
7	0.0	[196, 0]
8	0.0	[197, 0]
9	0.0	[198, 0]
10	0.0	[199, 0]
11	0.0	[200, 0]
12	0.0	[201, 0]
13	0.0	[202, 0]
14	0.0	[203, 0]
15	0.0	[204, 0]
16	0.0	[205, 0]
17	0.0	[206, 0]
18	0.0	[207, 0]
19	0.0	[224, 0, 64]
20	0.0	[225, 42, 69]
21	0.0	[226, 85, 74]
22	0.0	[227, 127, 79]
23	0.0	[228, 42, 85]
24	0.0	[229, 85, 90]
25	0.0	[230, 0, 64]
26	0.0	[231, 42, 69]
27	0.0	[232, 85, 74]
28	0.0	[233, 127, 79]
29	0.0	[234, 42, 85]
30	0.0	[235, 85, 90]
31	0.0	[236, 0, 64]
32	0.0	[237, 42, 69]
33	0.0	[238, 85, 74]
34	0.0	[239, 127, 79]


## Tools for working with the harmonic series

```harmonics(harmonic1, harmonic2, fund=1, reverse=False)```

The `harmonics()` function returns the harmonic series ratios between
two harmonic numbers. If 0 < harmonic1 < harmonic2 then the ratios will produce
the *overtone series*. Note that values in this series are now normalized to the first harmonic in the series, so the first number becomes 1 and each number above the first value is the ratio distance up from the first number to that harmonic:

In [8]:
musx.harmonics(8, 16)

[Fraction(1, 1),
 Fraction(9, 8),
 Fraction(5, 4),
 Fraction(11, 8),
 Fraction(3, 2),
 Fraction(13, 8),
 Fraction(7, 4),
 Fraction(15, 8),
 Fraction(2, 1)]

If (0 > harmonic1 > harmonic2) will produce [undertones](https://en.wikipedia.org/wiki/Undertone_series). See: [Harry Partch](https://en.wikipedia.org/wiki/Harry_Partch#Theory):

In [9]:
musx.harmonics(-8, -16)

[Fraction(1, 1),
 Fraction(8, 9),
 Fraction(4, 5),
 Fraction(8, 11),
 Fraction(2, 3),
 Fraction(8, 13),
 Fraction(4, 7),
 Fraction(8, 15),
 Fraction(1, 2)]

Note that if the "fundamental" is 1 then python Fractions are returned
to keep tuning ratios as accurate as possible. You can convert the series
to a specific fundamental in hertz using the function's 3rd argument *fund*:

In [10]:
musx.harmonics(8, 16, 220.0)

[220.0, 247.5, 275.0, 302.5, 330.0, 357.5, 385.0, 412.5, 440.0]

In [11]:
musx.harmonics(-8, -16, 440.0)

[440.0,
 391.1111111111111,
 352.0,
 320.0,
 293.3333333333333,
 270.7692307692308,
 251.42857142857142,
 234.66666666666666,
 220.0]

Normally overtone ratios are ascending and undertones are
decending.  If reverse is True then overtones are returned in reversed order 
(overtones descending, undertones ascending):

In [12]:
musx.harmonics(8, 16, 220.0, reverse=True)

[440.0, 412.5, 385.0, 357.5, 330.0, 302.5, 275.0, 247.5, 220.0]

In [13]:
musx.harmonics(-8, -16, 440.0, reverse=True)

[220.0,
 234.66666666666666,
 251.42857142857142,
 270.7692307692308,
 293.3333333333333,
 320.0,
 352.0,
 391.1111111111111,
 440.0]

### Playing the harmonic series

To play the harmonic series using MIDI we will need to use the musx.keynum() function to convert hertz values into floating point key numbers. This composer "transposes" the harmonics between h1 and h2 inclusive into list of floating point key numbers to play:

In [14]:
def playharms(score, fund, h1, h2, rhy, amp):
    freqs = musx.harmonics(h1, h2, fund)
    keynums = musx.keynum(freqs, filt=None)
    print("freqs:", freqs, "\nkeynums:", keynums)
    for k in keynums:
        m = musx.Note(time=score.now, duration=rhy, pitch=k, amplitude=amp)
        score.add(m)
        yield rhy
print('OK!')

OK!


Now play the overtones quanitzed to 1/8 tone tuning:

In [15]:
a = musx.MidiFile.metatrack(microdivs=4)
b = musx.Seq()
score = musx.Score(out=b)
score.compose([[0,    playharms(score, musx.hertz("C4"),  8,  16, .5, .5)],
               [.5*9, playharms(score, musx.hertz("C5"), -8, -16, .5, .5)]])
f=musx.MidiFile("harms.mid", [a,b]).write()
musx.playfile(f.pathname)

freqs: [261.6255653005986, 294.32876096317347, 327.0319566257483, 359.7351522883231, 392.43834795089793, 425.1415436134728, 457.84473927604756, 490.5479349386224, 523.2511306011972] 
keynums: [60.0, 62.039100017307746, 63.86313713864835, 65.51317942364757, 67.01955000865387, 68.4052766176931, 69.68825906469125, 70.88268714730222, 72.0]
freqs: [523.2511306011972, 465.11211608995313, 418.6009044809578, 380.5462768008707, 348.83408706746485, 322.0006957545829, 299.000646057827, 279.0672696539719, 261.6255653005986] 
keynums: [72.0, 69.96089998269225, 68.13686286135164, 66.48682057635243, 64.98044999134612, 63.594723382306896, 62.31174093530875, 61.11731285269778, 60.0]


## Example: harmonic primes

This example creates a 5 voice texture to perform two octaves of the the harmonic series starting on each new prime number in the series. The prime number also serves as the rhythm of each voice.

<img src="support/primeharmonics.png/>

In [16]:
def primevoice(score, fund, beat, harm1, harm2):
    ryth = beat * 4 
    for freq in musx.harmonics(harm1, harm2, fund=fund*harm1):
        k = musx.keynum(freq, filt=None)
        n = musx.Note(time=q.now, duration=ryth, pitch=k)
        score.add(n)
        yield ryth

In [17]:
a = musx.MidiFile.metatrack(microdivs=12)
b = musx.Seq()
q = musx.Score(out=b)
q.compose([ primevoice(q, musx.hertz("c1"), 1/p, p, p*4) for p in [2,3,5,7,11] ])
f = musx.MidiFile("harms.mid", [a, b]).write()
musx.playfile(f.pathname)

## Converting harmonics into tuning ratios, floating point intervals, and scales.

Composers often want to treat the distances between harmonics as *just intervals* that can be used to transpose any pitch by a just amount. Since just intervals are ratios in the harmonic series they will always involve microtones relative to 12-TET.

In [18]:
harmonics = [8, 9, 10, 11, 12, 13, 14, 15, 16]
print(harmonics)

[8, 9, 10, 11, 12, 13, 14, 15, 16]


To convert harmonic numbers into interval ratios, divide the harmonic numbers by the lowest harmonic. You can use floats or Fractions for this division. Fractions have the advantage of preserving the exact ratio value, e.g. 1/3 instead of 0.3333333... To divide a list of harmonic numbers you can use a comprehension or the *musx.divide()* function.

Example using Fractions:

In [19]:
from fractions import Fraction
ratios = musx.divide(harmonics, Fraction(8))
print(ratios)

[Fraction(1, 1), Fraction(9, 8), Fraction(5, 4), Fraction(11, 8), Fraction(3, 2), Fraction(13, 8), Fraction(7, 4), Fraction(15, 8), Fraction(2, 1)]


Example using floats:

In [20]:
print(musx.divide(harmonics, 8))

[1.0, 1.125, 1.25, 1.375, 1.5, 1.625, 1.75, 1.875, 2.0]


To convert harmonic ratios into 'semitone ratios', e.g. floating point intervals *sss.cc* where *sss* is the number of semitones and *cc* is the extra cents above it. Semitone intervals can be added rather than multiplied. 

The temper function converts a ratio into a semitonal ratios or a cent value:

```temper(ratio, div=12)```

*ratio* is the ratio to convert and *div* is the divisions per octave. A value of 12 will convert a ratio into a semitone interval *sss.cc*.  A value of 1200 will convert it into cents.

The semitone interval of a just fifth:

In [21]:
musx.temper(Fraction(3, 2))

7.019550008653875

The semitone interval of a just fourth:

In [22]:
musx.temper(Fraction(4,3))

4.980449991346124

A fifth plus a fourth equal an octave (semitone interval addition):

In [23]:
7.019550008653875 + 4.980449991346124

12.0

A div value of 1200 will convert the ratio into cents, in the case of cents you should probably also round to an integer:

In [ ]:
print(musx.temper(Fraction(3, 2), 1200))

print(round(musx.temper(Fraction(3, 2), 1200)))

Summary: Using temper we can convert a ratio interval into semitonal intervals so they can be added to key numbers rather than having to multiply by a hertz value:

In [25]:
print("ratios:", ratios)
semitones = musx.temper(ratios)
print("\nsemitones:", semitones)
print("\nkeynums:", [60 + i for i in semitones] )

ratios: [Fraction(1, 1), Fraction(9, 8), Fraction(5, 4), Fraction(11, 8), Fraction(3, 2), Fraction(13, 8), Fraction(7, 4), Fraction(15, 8), Fraction(2, 1)]

semitones: [0.0, 2.0391000173077485, 3.863137138648348, 5.513179423647567, 7.019550008653875, 8.405276617693106, 9.688259064691248, 10.88268714730222, 12.0]

keynums: [60.0, 62.039100017307746, 63.86313713864835, 65.51317942364757, 67.01955000865388, 68.4052766176931, 69.68825906469125, 70.88268714730222, 72.0]


### Microtonal Scales

To convert semitone intervals into a *scale* you need to determine the interval distances *between* adjacent semitone values. You can use the musx function *delta()* to get these differences:

In [26]:
print("semitones:", semitones)
intervals = musx.deltas(semitones)
print("\nintervals:", intervals)
print("\nsum to:", sum(intervals))

semitones: [0.0, 2.0391000173077485, 3.863137138648348, 5.513179423647567, 7.019550008653875, 8.405276617693106, 9.688259064691248, 10.88268714730222, 12.0]

intervals: [2.0391000173077485, 1.8240371213405995, 1.650042284999219, 1.5063705850063078, 1.3857266090392315, 1.2829824469981421, 1.1944280826109726, 1.1173128526977791]

sum to: 12.0


Now that we have an octave of the scale defined as deltas we can use the *scale()* function to create the scale on any key number we want!

This example produces a 4 octave scale starting on C3:

In [27]:
scale = musx.scale(48, len(intervals)*4+1, intervals)
print(scale)

[48, 50.039100017307746, 51.86313713864835, 53.513179423647564, 55.01955000865387, 56.405276617693104, 57.688259064691245, 58.88268714730222, 60.0, 62.039100017307746, 63.86313713864835, 65.51317942364757, 67.01955000865388, 68.40527661769312, 69.68825906469127, 70.88268714730224, 72.00000000000001, 74.03910001730776, 75.86313713864836, 77.51317942364757, 79.01955000865388, 80.40527661769312, 81.68825906469127, 82.88268714730224, 84.00000000000001, 86.03910001730776, 87.86313713864836, 89.51317942364757, 91.01955000865388, 92.40527661769312, 93.68825906469127, 94.88268714730224, 96.00000000000001]


In [28]:
def playscale(score, n, r, scale):
    #print(scale)
    for k in scale:
        #print(k)
        m = musx.Note(time=score.now, duration=r, pitch=k)
        score.add(m)
        yield r
print('OK!')

OK!


In [29]:
a = musx.MidiFile.metatrack(microdivs=4)
b = musx.Seq()
q = musx.Score(out=b)
l = len(scale)
c1 = playscale(q, l, .2, musx.cycle(scale, stop=l))
c2 = playscale(q, l, .2, musx.jumble(scale, stop=l))
c3 = playscale(q, l, .2, musx.cycle(scale[::-1], stop=l))
q.compose([[0 , c1], [.2*l, c2], [.2*l*2, c3]])
f = musx.MidiFile("harms.mid", [a, b]).write()
musx.playfile(f.pathname)
print(f.pathname)

harms.mid


## Example: Ben Johnston's blues scale from Suite for Microtonal Piano

The piano tuning for [Ben Johnston's](https://en.wikipedia.org/wiki/Ben_Johnston_(composer)) Suite for Microtonal Piano is taken from a selection of overtones in the fifth octave of the harmonics series based on C. The scale includes all the notes of the 4th octave harmonic series (8-16) plus some of the new harmonics appearing in the 5th octave: 17, 19, 21 and 27. The remaining new harmonics: 23, 25, 29, 31 were omitted, yielding a 12-note just chromatic tuning scale for the piano.

```
C    C#  D   Eb  E   F   F#  G   Ab  A   Bb  B   C  
[16, 17, 18, 19, 20, 21, 22, 24, 26, 27, 28, 30, 32] (the octave)
```

The Blues movement is in D dorian and also includes notes from the D chromatic scale. Dividing the C-based scale by 9/8 yields the D dorian tuning where D is 1/1 and 2/1:

The chromatic D dorian blues scale:

```
 D    D#     E     F    F#    G    Ab    A    Bb    B    C     C#    D
[1/1, 19/18, 10/9, 7/6, 11/9, 4/3, 13/9, 3/2, 14/9, 5/3, 16/9, 17/9, 2/1]
```

The diatonic D dorian blues scale is therefore:

```
 D    E     F    G    A    Bb    C     D 
[1/1, 10/9, 7/6, 4/3, 3/2, 14/9, 16/9, 2/1]
```

Pay special attention to the blue note F (7/6) which is the true "blues third" between harmonic 6 and 7 in 4th octave of the harmonic but "transposed" to D to provide a true blues third above the just dorian tonic D. Note that a second (wider) 11/9 third above D is also featured in the scale.

Here is a comparison of the just thirds with their equal tempered counterparts:

In [30]:
# equal tempered major third
print("ET M3:", musx.temper(2**(4/12)))
# just third between harmonic 9 and 11
print(" 11/9:", musx.temper(11/9))
# equal tempered minor third
print("ET m3:", musx.temper(2**(3/12)))
# just 'third' between harmonic 6 and 7 (blues third)
print("Blues:", musx.temper(7/6))

ET M3: 4.0
 11/9: 3.4740794063398206
ET m3: 2.9999999999999996
Blues: 2.6687090560373763


Follow the score while listening to Ben Johnston's "Blues" movement from Suite for Microtonal Piano:

In [31]:
%%bash
open "Johnston Suite for Microtonal Piano Blues.pdf"

In [32]:
from IPython.display import Audio
Audio('Johnston Suite for Microtonal Piano - II. Blues.mp3') # remote WAV file

Ben Johnston was on the composition faculty here at the UIUC from 1951 to 1986. He died just recently on July 21, 2019, in Deerfield Wisconsin.

## Listen to Ben Johnston's blues scale from Suite for Microtonal Piano

In [ ]:
from fractions import Fraction
#            D   E   F   F#  G   A   Bb  C   D
harmonics = [18, 20, 21, 22, 24, 27, 28, 32, 36] 

# Convert harmonic numbers to ratios 1/1 to 2/1 based on the lowest harmonic (18):
ratios = musx.divide(harmonics, Fraction(18,1))
print(ratios)

# Convert the ratios into semitones for working with midi:
semitones = musx.temper(ratios)
print(semitones)

# Convert from semitones above a starting keynumber to semitone between successive steps:
intervals = musx.deltas(semitones)
print(intervals)

scale = musx.scale(60, 8*3+1, intervals)
print(scale)

In [ ]:
scale

In [ ]:
a = musx.MidiFile.metatrack(microdivs=4)
b = musx.Seq()
q = musx.Score(out=b)
l = len(scale)
c1 = playscale(q, l, .25, musx.cycle(scale, stop=l))
c2 = playscale(q, l, .25, musx.jumble(scale, stop=l))
c3 = playscale(q, l, .25, musx.cycle(scale[::-1], stop=l))
q.compose([[0 , c1], [.25*l, c2], [.25*l*2, c3]])
f = musx.MidiFile("harms.mid", [a, b]).write()
print(f.pathname)
musx.playfile(f.pathname)

## In class exercise: play the pentatonic primes!

There is a beautiful pentatonic scale consisting of all the new prime numbered harmonics in the 5th octave of the harmonic series. What does this scale sound like?

<!--
harmonics = [17, 19, 23, 29, 31, 34]
print(harmonics)

Convert the harmonic numbers into ratios from 1/1 to 2/1 based on the lowest harmonic (17):
ratios = musx.divide(harmonics, 17)
print(ratios)

Convert the ratios into semitones for working with midi:
semitones = musx.temper(ratios)
print(semitones)

Convert from semitones above a starting keynumber to semitone between successive steps:
intervals = musx.deltas(semitones)
print(intervals)

Convert the interval steps into a full three octave scale based on key number 60:
scale = musx.scale(60, 15+1, intervals)
print(scale)
-->

Write the prime numbers in the 5th octave, include the octave to end it:

In [ ]:
harmonics = [17, 19, 23, 29, 31, 34]
print(harmonics)

Convert the harmonic numbers into ratios from 1/1 to 2/1 based on the lowest harmonic (17):

In [ ]:
ratios = musx.divide([17, 19, 23, 29, 31, 34], 17)
print(ratios)

Convert the ratios into semitones for working with midi:

In [ ]:
semitones = musx.temper(ratios)
print(semitones)

Convert from semitones above a starting key number to semitones between successive steps:

In [ ]:
intervals = musx.deltas(semitones)
print(intervals)

Convert the interval steps into a full three octave scale based on key number 60 and ending on keynum 96:

In [ ]:
scale = musx.scale(60, 15+1, intervals)
print(scale)

An algorithm to perform the scale:

In [ ]:
def primechime(score, numnotes, scale, rhy, dur, amp, chan):
    rhy = rhy * 2
    dur = dur * 2
    rhythms = musx.choose([rhy, [0, rhy/2 ], [0, rhy/3, (rhy/3)*2]], [6, 2, 1])
    size = len(scale)
    for _ in range(numnotes):
        r = next(rhythms)
        if musx.isnum(r):
            n = int(musx.rescale(musx.highran(), 0, 1, 0, size))
            k = scale[n]
            m = musx.Note(time=score.now, duration=rhy, pitch=k, amplitude=amp, instrument=chan)
            score.add(m)
        else:
            for t in r:
                n = int(musx.rescale(musx.highran(), 0, 1, 0, size))
                k = scale[n]
                m = musx.Note(time=score.now+t, duration=rhy, pitch=k, amplitude=amp, instrument=chan)
                score.add(m)
        yield rhy
print(primechime)

Create the two voice composition:

In [ ]:
from musx.midi.gm import MusicBox, TubularBells

a = musx.MidiFile.metatrack(ins={0: MusicBox, 4: TubularBells}, microdivs=4)
b = musx.Seq()
q = musx.Score(out=b)
q.compose([primechime(q, 60, scale, .25, 1, .6, 0),
           primechime(q, 30, musx.subtract(scale, 24) , .25*2, 1*2, .6, 4)])
f = musx.MidiFile("harms.mid", [a, b]).write()
print(f.pathname)
musx.playfile(f.pathname)

### Gamelan Scales

Try creating the Javanese pelog and slendro scales. Since there is no single tuning for these scales, try making Slendro a 5 tone scale in 5-TET tuning and Pelog a 7 tone scale in 9-TET tuning, where intervals are 1 1 2 1 1 1 2 (1)

<!-- 
slendro = [musx.temper(2 ** (i/5)) for i in range(6)]
pelog = [musx.temper(2 ** (i/9)) for i in [0, 1, 2, 4, 5, 6, 7, 9]]


slendro = [0.0, 2.4000000000000012, 4.8, 7.199999999999999, 9.6, 12.0]

pelog = [0.0, 1.3333333333333324, 2.666666666666666, 5.333333333333332, 
         6.666666666666667, 7.999999999999998, 9.333333333333334, 12.0]



from musx.midi.gm import MusicBox, TubularBells

#def playscale(q, n, r, scale):
#    #print(scale)
#    for k in scale:
#        #print(k)
#        m = musx.MidiNote(time=q.now, dur=r, key=k, tuning=4)
#        q.out.addevent(m)
#        yield r
        
a = musx.MidiFile.metatrack(ins={0: TubularBells}, microdivs=4)
b = musx.Seq()
q = musx.Score(out=b)
q.compose(playscale(q, 0, .4 , scale))
f = musx.MidiFile("harms1.mid", [a, b]).write()
print(f.pathname)
musx.playfile(f.pathname)
-->

In [ ]:
slendro = []
pelog = []